In [1]:
from datasets import load_dataset
from huggingface_hub import snapshot_download
from transformers import pipeline
import weblinx as wl
import torch
import re
import lxml
import sys
sys.path.append('D:\545_final\final project')
# print(sys.path)
from lxml import html
from lxml import etree
import weblinx as wl
import weblinx.utils.html as wh
import weblinx.utils.format as wlf
import tqdm
import copy
from copy import deepcopy
from bs4 import BeautifulSoup


from sentence_transformers.util import cos_sim
from weblinx_model.modeling.dmr.processing import build_formatters, build_records_for_single_turn, build_records_for_single_demo  # weblinx/modeling/dmr/processing.py




c:\Users\aswil\anaconda3\envs\glass_dots\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [3]:
# Load the validation split
valid = load_dataset("McGill-NLP/weblinx", split="validation")

# Download the input templates and use the LLaMA one
snapshot_download(
    "McGill-NLP/WebLINX", repo_type="dataset", allow_patterns="templates/*", local_dir="."
)
with open('templates/llama.txt') as f:
    template = f.read()

# To get the input text, simply pass a turn from the valid split to the template
turn = valid[0]
turn_text = template.format(**turn)

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): huggingface.co:443
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "GET /api/datasets/McGill-NLP/weblinx HTTP/1.1" 307 67
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "GET /api/datasets/McGill-NLP/WebLINX HTTP/1.1" 200 2412
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): s3.amazonaws.com:443
DEBUG:urllib3.connectionpool:https://s3.amazonaws.com:443 "HEAD /datasets.huggingface.co/datasets/datasets/McGill-NLP/weblinx/McGill-NLP/weblinx.py HTTP/1.1" 404 0
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "GET /api/datasets/McGill-NLP/weblinx HTTP/1.1" 307 67
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "GET /api/datasets/McGill-NLP/WebLINX HTTP/1.1" 200 2412
DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): huggingface.co:443
DEBUG:urllib3.connectionpool:https://huggingface.co:443 "HEAD /datasets/McGill-NLP/weblinx/resolve/e665e9ca7d823caa541e4de3acc046467c910e

In [4]:
def extract_uid(action):
    action_pattern = re.compile(r'\b\w+\(.*?\buid="([\w-]+)"\)')
    uid_match = action_pattern.search(action)
    if uid_match:
        return uid_match.group(1)
    else:
        return None

In [5]:
def find_element_by_uid(data, action):
    # Split the data based on the starting point of each candidate, which includes "(uid = "
    candidates = re.split(r'(?=\(uid\s*=\s*\w+-\w+-\w+\))', data)
    
    # Define a simpler regex to extract the desired details from a correctly identified candidate
    uid_pattern = re.compile(r'\(uid\s*=\s*([\w-]+)\)')
    tag_pattern = re.compile(r'\[\[tag\]\]\s*(\w+)')
    xpath_pattern = re.compile(r'\[\[xpath\]\]\s*([^[]+)')
    bbox_pattern = re.compile(r'\[\[bbox\]\]\s*x=([\d.]+)\s*y=([\d.]+)\s*width=([\d.]+)\s*height=([\d.]+)')
    attributes_pattern = re.compile(r'\[\[attributes\]\]\s*([^[]+)')

    # Process each candidate to find a match
    uid = extract_uid(action)
    for candidate in candidates:
        match_uid = uid_pattern.search(candidate)
        if match_uid and match_uid.group(1) == uid:
            # Extracting details only if the UID matches
            tag = tag_pattern.search(candidate).group(1)
            xpath = xpath_pattern.search(candidate).group(1).strip()
            bbox_match = bbox_pattern.search(candidate)
            attributes = attributes_pattern.search(candidate).group(1).strip()
            
            bbox_details = {
                "x": float(bbox_match.group(1)),
                "y": float(bbox_match.group(2)),
                "width": float(bbox_match.group(3)),
                "height": float(bbox_match.group(4))
            }
            
            return {
                "uid": uid,
                "tag": tag,
                "xpath": xpath,
                "bbox": bbox_details,
                "attributes": attributes
            }

    return None  # Return None if no matching UID is found

In [6]:
# This works on a valid for now.
def interpret_action(action):
    action_type = action.split("(")[0].strip()
    if action_type == "click":
        action_uid = extract_uid(action)
        
    elif action_type == "text_input":
        action_uid = extract_uid(action)
        input_pattern = re.compile(r'text="(.*?)"')
        input_match = input_pattern.search(action)
        output = input_match.group(1)
        
    elif action_type == "say":
        utterance_pattern = re.compile(r'utterance="(.*?)"\)')
        utterance_match = utterance_pattern.search(action)
        output = utterance_match.group(1)
        
    elif action_type == "submit":
        action_uid = extract_uid(action)
        
    elif action_type == "load":
        url_pattern = re.compile(r'url="(.*?)"')
        url_match = url_pattern.search(action)
        url = url_match.group(1)
        
    elif action_type == "scroll":
        scroll_pattern = re.compile(r'scroll\(x=(\d+), y=(\d+)\)')
        match = scroll_pattern.match(action)
        
        if match:
            x_value = int(match.group(1))
            y_value = int(match.group(2))
            
    elif action_type == "change":
        action_uid = extract_uid(action)
        change_pattern = re.compile(r'value="(.*?)"')
        change_match = change_pattern.search(action)
        change_val = change_match.group(1)
    else:
        pass

In [129]:
# Everything below this is for working with demos.
format_intent_input, _ = build_formatters()
uid_key = "data-webtasks-id"
# pick a demo name, this one is the one that is in Valid
demo_name = "apfyesq"
demo_choice = wl.Demonstration(name=demo_name, base_dir="wl_data/demonstrations/")
demo_list = wl.list_demonstrations("wl_data/demonstrations/")
for demo in demo_list:
    if demo.name == demo_name:
        break
else:
    print('fail')
replay = wl.Replay.from_demonstration(demo_choice)
print(replay)
a = build_records_for_single_demo(demo=demo_choice, format_intent_input=format_intent_input)

Replay(num_turns=46, created=unknown, demo_name=apfyesq, base_dir=wl_data/demonstrations/)


In [140]:
def extract_turn_properties(turn):
    #take a look in weblinx_model/weblinx/__init__.py for what any of these are
    info = {}
    info["type"] = turn.type
    if turn.type == "chat":
        # who is speaking, utterance = words to say
        if turn["speaker"] == "instructor": info["speaker"] = "instructor"
        else: info["speaker"] = "navigator"
        info["utterance"] = turn.utterance
    else:
        # Intent is action, important. none if its a chat turn
        info["intent"] = turn.intent
        info["metadata"] = turn.metadata
        info["url"] = turn.url
        info["tab_id"] = turn.tab_id
        info["viewport_height"] = turn.viewport_height
        info["viewport_width"] = turn.viewport_width
        info["mouse_x"] = turn.mouse_x
        info["mouse_y"] = turn.mouse_y
        info["client_x"] = turn.client_x
        info["zoom"] = turn.zoom
        # the element that is being acted upon if its a browser turn
        info["element"] = turn.element
        # if it's a browser turn, givs the properties of the action
        info["props"] = turn.props
        info["bboxes"] = turn.bboxes
        # can load this directly as the html
        info["html"] = turn.html
        # can also grab the html from the specific demo's html files
        info["html_path"] = turn.get_html_path()
        info["xpaths"] = turn.get_xpaths_dict()
    return info
        
        
        
        
    

In [116]:
# can get all browser turns
brows_turns = replay.filter_by_type("browser")
print(brows_turns)

[Turn(index=4, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=6, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=7, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=8, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=9, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=10, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=11, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=12, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=14, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=15, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=16, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=17, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=18, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=19, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=22, demo_name=apfyesq, base

In [143]:
for turn in replay:
    print(turn.element)
    # print("turn num: " + str(turn.index) + " " + turn.format_text(max_length=50))

None
None
None
None
None
None
{'attributes': {'class': 'searchbox form-search form-input', 'data-drupal-selector': 'edit-keys', 'data-ms-editor': 'true', 'data-webtasks-id': '67e2a5fb-8b1d-41a0', 'id': 'edit-keys', 'maxlength': '128', 'name': 'q', 'placeholder': 'What do you want to learn today?', 'size': '15', 'spellcheck': 'false', 'title': '', 'type': 'search', 'value': ''}, 'bbox': {'bottom': 688.2031154632568, 'height': 111.99999809265137, 'left': 524.5000076293945, 'right': 1121.500015258789, 'top': 576.2031173706055, 'width': 597.0000076293945, 'x': 524.5000076293945, 'y': 576.2031173706055}, 'innerHTML': '', 'outerHTML': '<input title="" class="searchbox form-search form-input" placeholder="What do you want to learn today?" data-drupal-selector="edit-keys" type="search" id="edit-keys" name="q" value="" size="15" maxlength="128" data-webtasks-id="67e2a5fb-8b1d-41a0" spellcheck="false" data-ms-editor="true">', 'tagName': 'INPUT', 'textContent': '', 'xpath': 'id("block-heroblock")

In [146]:
for turn in replay:
    #increase max_length for the full thing to output, but is basically pretty good for figuring out exactly what to do
    print("turn num: " + str(turn.index) + " " + turn.format_text(max_length=50))


turn num: 0 [instructor] -> SAY: Hello
turn num: 1 [navigator] -> SAY: Hi
turn num: 2 [instructor] -> SAY: Open Encyclopedia website.
turn num: 3 [navigator] -> SAY: Yes, sure
turn num: 4  -> LOAD: https://www.encyclopedia.com/, transition=typed, qualifiers=(from_address_bar)
turn num: 5 [instructor] -> SAY: Search for biotechnology
turn num: 6 [input]  -> CLICK
turn num: 7 [input]  -> PASTE: biotechnology
turn num: 8 [input]  -> TEXTINPUT: biotechnology
turn num: 9 [input]  -> CLICK
turn num: 10 [form]  -> SUBMIT
turn num: 11  -> LOAD: https://www.encyclopedia.com/gsearch?q=biotechnolo[...], transition=form_submit, qualifiers=()
turn num: 12 [html] Search Results | Encyclopedia.com 
(function(i,s,o... -> CLICK
turn num: 13 [instructor] -> SAY: Show me some option
turn num: 14 [div] ×search Encyclopedia New About 3,920 results (0.16... -> CLICK
turn num: 15 [b] Biotechnology -> COPY: Biotechnology | Encyclopedia.com
turn num: 16 [div] Search Results ×search Encyclopedia New About 3,92.

In [142]:
turn_props = extract_turn_properties(replay[7])
print(turn_props["xpaths"])
# print(turn_props.keys())
# print(turn_props["html"])

{'8f58fc5c-481b-4f6f': '/html/head', 'e3d7bf6b-c474-47bc': '/html/head/style[1]', '47a0173d-4da8-470c': '/html/head/style[2]', '051655fe-f85f-4198': '/html/head/style[3]', 'c132f59c-2887-435c': '/html/head/meta[1]', 'ae72c111-f297-4d26': '/html/head/meta[2]', 'dc4a4041-2cbb-47f3': '/html/head/link[1]', '593e9849-e146-43f5': '/html/head/link[2]', '9a975e7d-133d-4b7b': '/html/head/meta[3]', 'fbf24ec7-7060-4692': '/html/head/meta[4]', '1c954a87-40ba-4b70': '/html/head/meta[5]', 'eba39b5b-ff87-406c': '/html/head/meta[6]', 'aebd4da0-3f0f-49bf': '/html/head/meta[7]', '06fe1174-49bd-468d': '/html/head/meta[8]', 'a8e87b43-7959-4646': '/html/head/meta[9]', '0a10c946-dad7-4e61': '/html/head/link[3]', 'f7bd0822-8cea-425b': '/html/head/link[4]', '3552e192-b58f-4e43': '/html/head/title', '86bbb3fa-4243-42c8': '/html/head/script[1]', 'b682dd63-3073-40ea': '/html/head/script[2]', 'b238913e-0c94-4993': '/html/head/script[3]', 'adab72bb-8c8f-4518': '/html/head/script[4]', '0a26491e-e27a-4a76': '/html/h

In [74]:
print(replay[0].intent)

None


In [76]:
print(replay.list_urls())

['https://www.encyclopedia.com/science-and-technology/biology-and-genetics/biology-general/cloning', 'https://www.encyclopedia.com/gsearch?q=biotechnology', 'https://www.encyclopedia.com/', 'https://www.encyclopedia.com/people/science-and-technology/genetics-and-genetic-engineering-biographies/biotechnology']


In [49]:
turns = []
for i in range(46):
    curr_turn = wl.Turn.from_replay(replay = replay, index = i)
    turns.append(curr_turn)
    print(curr_turn.intent)




None
None
None
None
load
None
click
paste
textInput
click
submit
load
click
None
click
copy
click
copy
click
copy
None
None
click
None
click
None
click
copy
None
None
click
copy
None
None
click
copy
None
None
None
click
click
None
click
copy
None
None


In [52]:
for i in range(46):
    print("turn number: " + str(i), turns[i].format_text())

turn number: 0 [instructor] -> SAY: Hello
turn number: 1 [navigator] -> SAY: Hi
turn number: 2 [instructor] -> SAY: Open Encyclopedia website.
turn number: 3 [navigator] -> SAY: Yes, sure
turn number: 4  -> LOAD: https://www.encyclopedia.com/, transition=typed, qualifiers=(from_address_bar)
turn number: 5 [instructor] -> SAY: Search for biotechnology
turn number: 6 [input]  -> CLICK
turn number: 7 [input]  -> PASTE: biotechnology
turn number: 8 [input]  -> TEXTINPUT: biotechnology
turn number: 9 [input]  -> CLICK
turn number: 10 [form]  -> SUBMIT
turn number: 11  -> LOAD: https://www.encyclopedia.com/gsearch?q=biotechnolo[...], transition=form_submit, qualifiers=()
turn number: 12 [html] Search Results | Encyclopedia.com 
(function(i,s,o... -> CLICK
turn number: 13 [instructor] -> SAY: Show me some option
turn number: 14 [div] ×search Encyclopedia New About 3,920 results (0.16... -> CLICK
turn number: 15 [b] Biotechnology -> COPY: Biotechnology | Encyclopedia.com
turn number: 16 [div] 

In [54]:
for i in range(46):
    if turns[i].has_html():
        print("turn number: " + str(i), turns[i].get_html_path())

turn number: 6 wl_data\demonstrations\apfyesq\pages\page-1-0.html
turn number: 7 wl_data\demonstrations\apfyesq\pages\page-3-0.html
turn number: 8 wl_data\demonstrations\apfyesq\pages\page-2-0.html
turn number: 9 wl_data\demonstrations\apfyesq\pages\page-4-0.html
turn number: 10 wl_data\demonstrations\apfyesq\pages\page-5-0.html
turn number: 11 wl_data\demonstrations\apfyesq\pages\page-5-1.html
turn number: 12 wl_data\demonstrations\apfyesq\pages\page-7-0.html
turn number: 14 wl_data\demonstrations\apfyesq\pages\page-9-0.html
turn number: 15 wl_data\demonstrations\apfyesq\pages\page-11-0.html
turn number: 16 wl_data\demonstrations\apfyesq\pages\page-12-0.html
turn number: 17 wl_data\demonstrations\apfyesq\pages\page-14-0.html
turn number: 18 wl_data\demonstrations\apfyesq\pages\page-15-0.html
turn number: 19 wl_data\demonstrations\apfyesq\pages\page-17-0.html
turn number: 22 wl_data\demonstrations\apfyesq\pages\page-21-0.html
turn number: 24 wl_data\demonstrations\apfyesq\pages\page-26

In [57]:
print(replay.filter_by_type("browser"))
print(replay.filter_by_type("chat"))

[Turn(index=4, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=6, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=7, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=8, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=9, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=10, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=11, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=12, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=14, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=15, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=16, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=17, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=18, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=19, demo_name=apfyesq, base_dir=wl_data/demonstrations/), Turn(index=22, demo_name=apfyesq, base

In [148]:
#not important rn
# b = build_records_for_single_turn(turn=a[1], replay=a, format_intent_input=format_intent_input, uid_key=uid_key)
# print(b)